In [1]:
import sys
sys.path.append('/home/is/akiyoshi-n/my-project')

In [2]:
import os
# 使用するGPUを指定. この環境変数の場所は，pytorchをimportする前に入れる
os.environ["CUDA_VISIBLE_DEVICES"] = "0"
from pathlib import Path
from datetime import datetime
from src.my_project.dataset import load_dataset_4class_Multi_classification, split_test_data_stratify, load_text_dataset, split_multilabel_data
from src.my_project.train_v2 import MultiClassClassifier
from sklearn.model_selection import train_test_split
from src.my_project.dataset import load_multiclass_dataset
import wandb
import numpy as np
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score

In [3]:
DATASET_PATH = Path('/home/is/akiyoshi-n/my-project/data')
# 本日の日付
timestamp = datetime.now().strftime("%Y-%m-%d")
# 出力先ディレクトリ
output_dir = Path('/home/is/akiyoshi-n/my-project/outputs/{}'.format(timestamp))
# モデル出力先ディレクトリ
output_model_dir = Path('/home/is/akiyoshi-n/my-project/outputs_model')

### パラメータの設定

In [4]:
# 最大トークン数
MAX_LEN = 128
# バッチサイズ
BATCH_SIZE = 16
# BATCH_SIZE = 8
# エポック数
NUM_EPOCHS = 100
# 学習率
LEARNING_RATE = 2e-5
# LEARNING_RATE = 9.316263656504444e-05
# Cross Validation時のFold数
NUM_FOLDS = 5
# 早期停止のための忍耐値
PATIENCE = 4
# 乱数シード
SEED = 2024
# クラス数
NUM_LABELS = 4
# 閾値
THRESH = 0.5

In [5]:
# データの読み込み
data, class_name = load_dataset_4class_Multi_classification(f"{DATASET_PATH}/lifestory_GPT+human_annotation.xlsx")

In [6]:
len(data['texts'])

1000

In [7]:
len(data['labels'][0])

4

In [8]:
data_labels_np = np.array(data['labels'])
data_labels_np.sum(axis=0)

array([ 57, 153, 340, 451])

### モデル精度評価

In [9]:
# 東北大BERT-v3
MODEL_NAME = 'cl-tohoku/bert-base-japanese-v3'
Classifier_model = MultiClassClassifier(model_name = MODEL_NAME, num_labels=NUM_LABELS, seed=SEED, thresh=THRESH)

In [10]:
# 訓練データと評価データを辞書型で抽出
train_dataset = {
    'texts': [data['texts'][i] for i in range(900)],
    'labels': [data['labels'][i] for i in range(900)]
}
eval_dataset = {
    'texts': [data['texts'][i] for i in range(900, 1100)],
    'labels': [data['labels'][i] for i in range(900, 1100)]
}

In [11]:
trainer = Classifier_model.train_model(train_dataset, eval_dataset, MAX_LEN, NUM_EPOCHS, LEARNING_RATE, BATCH_SIZE, PATIENCE, output_dir, project_name='MultiClassification', run_name='test')

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at cl-tohoku/bert-base-japanese-v3 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Parameter 'fn_kwargs'={'tokenizer': BertJapaneseTokenizer(name_or_path='cl-tohoku/bert-base-japanese-v3', vocab_size=32768, model_max_length=512, is_fast=False, padding_side='right', truncation_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
	0: AddedToken("[PAD]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	1: AddedToken("[UNK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	2: AddedToken("[CLS]", rstrip=False, lstrip=False, single_word=False, normalized=False,

Map:   0%|          | 0/900 [00:00<?, ? examples/s]

Map:   0%|          | 0/200 [00:00<?, ? examples/s]

In [12]:
predictions = Classifier_model.predict(trainer, eval_dataset, MAX_LEN)

Map:   0%|          | 0/200 [00:00<?, ? examples/s]

In [13]:
predictions

array([[0., 0., 1., 0.],
       [0., 0., 0., 1.],
       [0., 0., 1., 0.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.],
       [0., 0., 1., 0.],
       [0., 0., 1., 0.],
       [0., 0., 0., 1.],
       [0., 0., 1., 0.],
       [0., 0., 1., 0.],
       [0., 0., 1., 0.],
       [0., 0., 1., 0.],
       [0., 1., 0., 0.],
       [0., 0., 1., 0.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.],
       [1., 0., 0., 0.],
       [0., 0., 0., 1.],
       [0., 0., 1., 0.],
       [0., 0., 1., 0.],
       [0., 0., 0., 1.],
       [0., 0., 1., 0.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.],
       [0., 0., 1., 0.],
       [0., 0., 1., 0.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.],
       [0., 0., 1., 0.],
       [0., 0., 0., 1.],
       [0., 0., 1., 0.],
       [0., 0., 0., 1.],
       [0., 0., 1., 0.],
       [0., 0., 1., 0.],


In [24]:
from transformers import AutoTokenizer
from src.my_project.dataset import preprocess_for_Trainer
import numpy as np
import torch
# tokenizerの定義
tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)
eval_dataset_use = preprocess_for_Trainer(eval_dataset, tokenizer, max_len=MAX_LEN)
predictions = trainer.predict(eval_dataset_use)

# predictions.predictionsにsigmoid関数を適用し，確率に変換
predictions = torch.sigmoid(torch.from_numpy(predictions.predictions))
thresh = 0.5
# predictions = torch.where(predictions > THRESH, 1, 0)
predictions_label = (predictions>thresh).float()

Map:   0%|          | 0/200 [00:00<?, ? examples/s]

In [25]:
type(predictions)

torch.Tensor

In [26]:
predictions[0]

tensor([0.0440, 0.0457, 0.3518, 0.3285])

In [23]:
if torch.sum(predictions[0]) == 0:
    print(True)

True


In [31]:
predictions_label[0]

tensor([0., 0., 0., 0.])

In [32]:
a[1]

array([0., 0., 0., 1.])

In [33]:
max_index = torch.argmax(predictions[0])
max_index
a[0][max_index] = 1
a[1][:-1] = predictions_label[0][:-1]

wandb: Network error (ReadTimeout), entering retry loop.


In [17]:
a = np.zeros((5,4))
for i in range(5):
    a[i] = predictions[i]

In [19]:
type(a)

numpy.ndarray

In [1]:
predictions

NameError: name 'predictions' is not defined

In [26]:
eval_dataset_use

Dataset({
    features: ['texts', 'labels', 'input_ids', 'token_type_ids', 'attention_mask'],
    num_rows: 200
})

In [21]:
from transformers import AutoTokenizer
from src.my_project.dataset import preprocess_for_Trainer
import numpy as np
import torch
# tokenizerの定義
tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)
# データセットの前処理
eval_dataset_use = preprocess_for_Trainer(eval_dataset, tokenizer, max_len=MAX_LEN)
predictions = trainer.predict(eval_dataset_use)
# predictions.predictionsにsigmoid関数を適用し，確率に変換
predictions = torch.sigmoid(torch.from_numpy(predictions.predictions))
# 0.5以上の確率を1，それ以外を0に変換
thresh = 0.5
# predictions = torch.where(predictions > THRESH, 1, 0)
predictions = (predictions>thresh).float()

Map:   0%|          | 0/200 [00:00<?, ? examples/s]

In [43]:
# 保存したTrainerを読み込む
model = AutoModelForSequenceClassification.from_pretrained('/home/is/akiyoshi-n/my-project/outputs/2024-02-04/cl-tohoku/bert-base-japanese-v32024-02-04T16-22-24/checkpoint-285')
trainer_v2 = Trainer(model=model)

In [19]:
import torch
for i in range(100):
    if torch.sum(predictions[i]) == 0:
        print(True)
        print(predictions[i])

True
tensor([0., 0., 0., 0.])
True
tensor([0., 0., 0., 0.])
True
tensor([0., 0., 0., 0.])
True
tensor([0., 0., 0., 0.])
True
tensor([0., 0., 0., 0.])
True
tensor([0., 0., 0., 0.])
True
tensor([0., 0., 0., 0.])
True
tensor([0., 0., 0., 0.])
True
tensor([0., 0., 0., 0.])
True
tensor([0., 0., 0., 0.])
True
tensor([0., 0., 0., 0.])


In [55]:
# trainerの予測値とeval_dataset['labels']のAccuracyとF1を出す
from sklearn.metrics import accuracy_score, f1_score
accuracy = accuracy_score(eval_dataset['labels'], predictions)
f1 = f1_score(eval_dataset['labels'], predictions, average='macro')
print(f'Accuracy: {accuracy:.4f}')
print(f'F1: {f1:.4f}')

Accuracy: 0.6850
F1: 0.6169


In [10]:
prediction = Classifier_model.predict(trainer, eval_dataset, MAX_LEN)

Map:   0%|          | 0/200 [00:00<?, ? examples/s]

In [13]:
prediction.label_ids

200

In [10]:
# 評価データでの評価
Classifier_model.evaluation(trainer, eval_dataset, MAX_LEN)

Map:   0%|          | 0/200 [00:00<?, ? examples/s]

{'eval_loss': 0.33989983797073364,
 'eval_accuracy': 0.545,
 'eval_f1': 0.5774035592587015,
 'eval_runtime': 0.8056,
 'eval_samples_per_second': 248.263,
 'eval_steps_per_second': 6.207,
 'epoch': 10.0}

### Add data

In [11]:
# add_data
add_dataset = load_text_dataset(f"{DATASET_PATH}/add_data_sub.txt.xlsx")

In [12]:
len(add_dataset['texts'])

6887

In [13]:
a = Classifier_model.get_additional_data(trainer, add_dataset, MAX_LEN)

Map:   0%|          | 0/6887 [00:00<?, ? examples/s]

In [14]:
a

tensor([[0.5022, 0.8367, 0.2520, 0.0895],
        [0.8590, 0.6207, 0.3415, 0.0363],
        [0.1242, 0.4935, 0.5855, 0.0768],
        ...,
        [0.6197, 0.7912, 0.1539, 0.0564],
        [0.5725, 0.9073, 0.2780, 0.0567],
        [0.1522, 0.9243, 0.1656, 0.1490]])

In [29]:
# 値が0.9以上かつ0.1未満しかない行を抽出
# 各要素が0.9以上または，0.1未満かどうかのブール値テンソル
b = (a >= 0.7) | (a < 0.3)
# 各行の要素がすべてTrueかどうかのブール値テンソル
c = b.all(axis=1)
# 抽出
len(a[c])

1917

In [30]:
a[c]

tensor([[0.2821, 0.2148, 0.2704, 0.1981],
        [0.0244, 0.0890, 0.0567, 0.8004],
        [0.0224, 0.0437, 0.0637, 0.7985],
        ...,
        [0.2196, 0.9242, 0.2450, 0.0725],
        [0.2991, 0.9164, 0.1451, 0.0792],
        [0.1522, 0.9243, 0.1656, 0.1490]])

In [28]:
# データを抽出
add_dataset['texts'][c]

TypeError: only integer tensors of a single element can be converted to an index

In [25]:
from collections import OrderedDict

# 文字列のリストを取得
texts = add_dataset['texts']

# OrderedDictを使用して重複を削除（順序を保持）
unique_texts = list(OrderedDict.fromkeys(texts))

# 新しい辞書を作成して結果を格納
new_add_dataset = {'texts': unique_texts}

In [26]:
a, b, c = Classifier_model.get_additional_data(trainer, new_add_dataset, MAX_LEN)

Map:   0%|          | 0/6768 [00:00<?, ? examples/s]

In [27]:
a

{'texts': ['舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  'ディズニーランドホテルなう。',
  'ディズニーランドホテルなう。',
  'ディズニーランドホテルなう。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  'ディズニーランドホテルなう。',
  'ディズニーランドホテルなう。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  'ディズニーランドホテルなう。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  'ディズニーランドホテルなう。',
  'ディズニーランドホテルなう。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  'ディズニーランドホテルなう。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  'ディズニーランドホテルなう。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  '舞浜地ビールなう。奈緒ちゃんの粋な計らい。',
  'ディズニーランドホテルなう。',
  '舞浜地ビールなう。奈緒ち

In [ ]:
wandb.finish()

### Cross Validation

In [6]:
# データの読み込み
data, class_name = load_dataset_4class_Multi_classification(f"{DATASET_PATH}/lifestory_GPT+human_annotation.xlsx")

In [7]:
# testデータと訓練に使用するデータに分割
dataset, test_data = split_multilabel_data(data=data, test_size=0.2, SEED=SEED)

In [9]:
print(np.array(dataset['labels']).sum(axis=0))
print(np.array(test_data['labels']).sum(axis=0))

[ 49 125 279 374]
[12 31 70 93]


In [10]:
# 東北大BERT-v3
MODEL_NAME = 'cl-tohoku/bert-base-japanese-v3'
Classifier_model = MultiClassClassifier(model_name=MODEL_NAME, num_labels=NUM_LABELS, seed=SEED, thresh=THRESH)

In [11]:
result = Classifier_model.cross_validation(dataset, test_data, MAX_LEN, NUM_EPOCHS, LEARNING_RATE, BATCH_SIZE, PATIENCE, NUM_FOLDS, output_dir, project_name='normal_data_4class_weight')

-----------------Fold: 1-----------------


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at cl-tohoku/bert-base-japanese-v3 and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Parameter 'fn_kwargs'={'tokenizer': BertJapaneseTokenizer(name_or_path='cl-tohoku/bert-base-japanese-v3', vocab_size=32768, model_max_length=512, is_fast=False, padding_side='right', truncation_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
	0: AddedToken("[PAD]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	1: AddedToken("[UNK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	2: AddedToken("[CLS]", rstrip=False, lstrip=False, single_word=False, normalized=False,

Map:   0%|          | 0/641 [00:00<?, ? examples/s]

Map:   0%|          | 0/158 [00:00<?, ? examples/s]

Map:   0%|          | 0/201 [00:00<?, ? examples/s]

...

Map:   0%|          | 0/642 [00:00<?, ? examples/s]

Map:   0%|          | 0/157 [00:00<?, ? examples/s]

wandb: WARNING Source type is set to 'repo' but some required information is missing from the environment. A job will not be created from this run. See https://docs.wandb.ai/guides/launch/create-job


Map:   0%|          | 0/201 [00:00<?, ? examples/s]

{'accuracy': 0.6231884057971014, 'macro_f1': 0.4831700258418464, 'class_f1': [0.286, 0.475, 0.377, 0.795], 'class_recall': [0.2, 0.609, 0.244, 0.889], 'class_precision': [0.5, 0.389, 0.833, 0.719]}


In [13]:
# 重みなしの場合の結果（cv=5）
average_accuracy = round(sum(d['accuracy'] for d in result)/len(result), 3)
average_macro_f1 = round(sum(d['macro_f1'] for d in result)/len(result), 3)
# クラスごとの平均値を計算
average_class_f1 = [round(sum(d['class_f1'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_f1']))]
average_class_recall = [round(sum(d['class_recall'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_recall']))]
average_class_precision = [round(sum(d['class_precision'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_precision']))]
print("Average accuracy:", average_accuracy)
print("Average Macro f1:", average_macro_f1)
print("Average Class f1:", average_class_f1)
print("Average Class recall:", average_class_recall)
print("Average Class precision:", average_class_precision)

Average accuracy: 0.627
Average Macro f1: 0.504
Average Class f1: [0.234, 0.438, 0.561, 0.781]
Average Class recall: [0.158, 0.577, 0.441, 0.834]
Average Class precision: [0.483, 0.354, 0.81, 0.737]


In [11]:
# 重みなしの場合の結果（cv=5）
average_accuracy = round(sum(d['accuracy'] for d in result)/len(result), 3)
average_macro_f1 = round(sum(d['macro_f1'] for d in result)/len(result), 3)
# クラスごとの平均値を計算
average_class_f1 = [round(sum(d['class_f1'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_f1']))]
average_class_recall = [round(sum(d['class_recall'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_recall']))]
average_class_precision = [round(sum(d['class_precision'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_precision']))]
print("Average accuracy:", average_accuracy)
print("Average Macro f1:", average_macro_f1)
print("Average Class f1:", average_class_f1)
print("Average Class recall:", average_class_recall)
print("Average Class precision:", average_class_precision)

Average accuracy: 0.579
Average Macro f1: 0.484
Average Class f1: [0.23, 0.348, 0.576, 0.782]
Average Class recall: [0.197, 0.437, 0.469, 0.851]
Average Class precision: [0.479, 0.29, 0.75, 0.725]


In [23]:
# 重みありの場合の結果（cv=5）
average_accuracy = round(sum(d['accuracy'] for d in result)/len(result), 3)
average_macro_f1 = round(sum(d['macro_f1'] for d in result)/len(result), 3)
# クラスごとの平均値を計算
average_class_f1 = [round(sum(d['class_f1'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_f1']))]
average_class_recall = [round(sum(d['class_recall'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_recall']))]
average_class_precision = [round(sum(d['class_precision'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_precision']))]
print("Average accuracy:", average_accuracy)
print("Average Macro f1:", average_macro_f1)
print("Average Class f1:", average_class_f1)
print("Average Class recall:", average_class_recall)
print("Average Class precision:", average_class_precision)

Average accuracy: 0.67
Average Macro f1: 0.543
Average Class f1: [0.3, 0.376, 0.694, 0.801]
Average Class recall: [0.266, 0.431, 0.581, 0.873]
Average Class precision: [0.408, 0.402, 0.883, 0.744]


### Cross validation LLM add data

In [14]:
# データの読み込み
data, class_name = load_dataset_4class_Multi_classification(f"{DATASET_PATH}/lifestory_GPT+human_annotation.xlsx")

In [15]:
# データの読み込み
data_add, class_name_add = load_dataset_4class_Multi_classification(f"{DATASET_PATH}/lifestory_GPT+human_annotation_2023_season2.xlsx")

In [16]:
# testデータと訓練に使用するデータに分割
dataset, test_data = split_multilabel_data(data=data, test_size=0.2, SEED=SEED)

In [17]:
# data_addをの中から500件だけ抽出（stratifiedを用いて）
data_add_500, _ = split_multilabel_data(data=data_add, test_size=0.6, SEED=SEED)

In [18]:
len(data_add_500['texts'])

513

In [19]:
# 東北大BERT-v3
MODEL_NAME = 'cl-tohoku/bert-base-japanese-v3'
Classifier_model = MultiClassClassifier(model_name=MODEL_NAME, num_labels=NUM_LABELS, seed=SEED, thresh=THRESH)

### 予測実行

In [20]:
result = Classifier_model.cross_validation_add_dataset(dataset, data_add_500, test_data, MAX_LEN, NUM_EPOCHS, LEARNING_RATE, BATCH_SIZE, PATIENCE, NUM_FOLDS, output_dir, project_name='normal_data_4class_weight')

-----------------Fold: 1-----------------


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at cl-tohoku/bert-base-japanese-v3 and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Map:   0%|          | 0/1154 [00:00<?, ? examples/s]

Map:   0%|          | 0/158 [00:00<?, ? examples/s]

wandb: WARNING Source type is set to 'repo' but some required information is missing from the environment. A job will not be created from this run. See https://docs.wandb.ai/guides/launch/create-job


...

Map:   0%|          | 0/1155 [00:00<?, ? examples/s]

Map:   0%|          | 0/157 [00:00<?, ? examples/s]

wandb: WARNING Source type is set to 'repo' but some required information is missing from the environment. A job will not be created from this run. See https://docs.wandb.ai/guides/launch/create-job


Map:   0%|          | 0/201 [00:00<?, ? examples/s]

{'accuracy': 0.6907894736842105, 'macro_f1': 0.5908459736487848, 'class_f1': [0.333, 0.508, 0.692, 0.829], 'class_recall': [0.333, 0.682, 0.551, 0.861], 'class_precision': [0.333, 0.405, 0.931, 0.8]}


In [21]:
# 重みなしの場合の結果（cv=5）
average_accuracy = round(sum(d['accuracy'] for d in result)/len(result), 3)
average_macro_f1 = round(sum(d['macro_f1'] for d in result)/len(result), 3)
# クラスごとの平均値を計算
average_class_f1 = [round(sum(d['class_f1'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_f1']))]
average_class_recall = [round(sum(d['class_recall'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_recall']))]
average_class_precision = [round(sum(d['class_precision'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_precision']))]
print("Average accuracy:", average_accuracy)
print("Average Macro f1:", average_macro_f1)
print("Average Class f1:", average_class_f1)
print("Average Class recall:", average_class_recall)
print("Average Class precision:", average_class_precision)

Average accuracy: 0.67
Average Macro f1: 0.557
Average Class f1: [0.269, 0.473, 0.692, 0.793]
Average Class recall: [0.245, 0.52, 0.612, 0.852]
Average Class precision: [0.302, 0.447, 0.839, 0.746]


In [13]:
# 重みなしの場合の結果（cv=5）
average_accuracy = round(sum(d['accuracy'] for d in result)/len(result), 3)
average_macro_f1 = round(sum(d['macro_f1'] for d in result)/len(result), 3)
# クラスごとの平均値を計算
average_class_f1 = [round(sum(d['class_f1'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_f1']))]
average_class_recall = [round(sum(d['class_recall'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_recall']))]
average_class_precision = [round(sum(d['class_precision'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_precision']))]
print("Average accuracy:", average_accuracy)
print("Average Macro f1:", average_macro_f1)
print("Average Class f1:", average_class_f1)
print("Average Class recall:", average_class_recall)
print("Average Class precision:", average_class_precision)

Average accuracy: 0.616
Average Macro f1: 0.567
Average Class f1: [0.449, 0.376, 0.673, 0.769]
Average Class recall: [0.427, 0.433, 0.573, 0.836]
Average Class precision: [0.521, 0.342, 0.831, 0.716]


In [11]:
# 重みなしの場合の結果（cv=5）
average_accuracy = round(sum(d['accuracy'] for d in result)/len(result), 3)
average_macro_f1 = round(sum(d['macro_f1'] for d in result)/len(result), 3)
# クラスごとの平均値を計算
average_class_f1 = [round(sum(d['class_f1'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_f1']))]
average_class_recall = [round(sum(d['class_recall'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_recall']))]
average_class_precision = [round(sum(d['class_precision'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_precision']))]
print("Average accuracy:", average_accuracy)
print("Average Macro f1:", average_macro_f1)
print("Average Class f1:", average_class_f1)
print("Average Class recall:", average_class_recall)
print("Average Class precision:", average_class_precision)

Average accuracy: 0.598
Average Macro f1: 0.568
Average Class f1: [0.476, 0.379, 0.666, 0.75]
Average Class recall: [0.569, 0.429, 0.573, 0.796]
Average Class precision: [0.429, 0.348, 0.801, 0.714]


### 予測用，全データを学習データにして予測

In [9]:
# データの読み込み
data, class_name = load_dataset_4class_Multi_classification(f"{DATASET_PATH}/lifestory_GPT+human_annotation.xlsx")

In [10]:
# データの読み込み
data_add, class_name_add = load_dataset_4class_Multi_classification(f"{DATASET_PATH}/lifestory_GPT+human_annotation_2023_season2.xlsx")

In [11]:
# testデータと訓練に使用するデータに分割
dataset, eval_data = split_multilabel_data(data=data, test_size=0.2, SEED=SEED)

In [12]:
print(np.array(dataset['labels']).sum(axis=0))
print(np.array(eval_data['labels']).sum(axis=0))
print(np.array(data_add['labels']).sum(axis=0))

[ 46 122 272 361]
[11 31 68 90]
[ 92 333 528 513]


In [13]:
# 東北大BERT-v3
MODEL_NAME = 'cl-tohoku/bert-base-japanese-v3'
Classifier_model = MultiClassClassifier(model_name=MODEL_NAME, num_labels=NUM_LABELS, seed=SEED, thresh=THRESH)

In [14]:
# 学習を行う
trainer = Classifier_model.train_model_adding_data(dataset, eval_data, data_add, MAX_LEN, NUM_EPOCHS, LEARNING_RATE, BATCH_SIZE, PATIENCE, output_dir)

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at cl-tohoku/bert-base-japanese-v3 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Parameter 'fn_kwargs'={'tokenizer': BertJapaneseTokenizer(name_or_path='cl-tohoku/bert-base-japanese-v3', vocab_size=32768, model_max_length=512, is_fast=False, padding_side='right', truncation_side='right', special_tokens={'unk_token': '[UNK]', 'sep_token': '[SEP]', 'pad_token': '[PAD]', 'cls_token': '[CLS]', 'mask_token': '[MASK]'}, clean_up_tokenization_spaces=True),  added_tokens_decoder={
	0: AddedToken("[PAD]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	1: AddedToken("[UNK]", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	2: AddedToken("[CLS]", rstrip=False, lstrip=False, single_word=False, normalized=False,

Map:   0%|          | 0/2060 [00:00<?, ? examples/s]

Map:   0%|          | 0/193 [00:00<?, ? examples/s]

In [15]:
trainer

In [16]:
from src.my_project.dataset import load_dataset_4class_Multi_classification, load_emotion_text_dataset
data_2019_3 = load_emotion_text_dataset(f"{DATASET_PATH}/downloaded_files/LifeStory_2019_season3.xlsx")

In [17]:
dataset = data_2019_3[0]

In [18]:
from src.my_project.dataset import preprocess_for_Trainer

In [19]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer

In [31]:
# tokenizerの定義
tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)

In [32]:
data = preprocess_for_Trainer(dataset, tokenizer, max_len=MAX_LEN)

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

In [34]:
result = trainer.predict(data)

In [35]:
result

PredictionOutput(predictions=array([[-0.77591556,  3.1995714 , -0.861807  , -3.6417613 ],
       [-3.8913262 , -0.43234074, -1.0913117 , -0.94472384],
       [-4.3231425 , -2.1194189 , -1.7114981 ,  0.34040365],
       ...,
       [-3.1336257 ,  1.51834   ,  0.28114724, -3.1975513 ],
       [-4.252631  , -3.7528899 , -2.7075615 ,  2.1905224 ],
       [-4.53362   , -0.9972997 , -1.7349123 , -0.26531786]],
      dtype=float32), label_ids=None, metrics={'test_runtime': 8.9297, 'test_samples_per_second': 111.986, 'test_steps_per_second': 7.055})

In [36]:
# 東北大BERT-v3
MODEL_NAME = 'cl-tohoku/bert-base-japanese-v3'
p = MultiClassClassifier(model_name=MODEL_NAME, num_labels=NUM_LABELS, seed=SEED, thresh=THRESH)

In [39]:
result = p.predict(trainer, dataset, MAX_LEN)

Map:   0%|          | 0/1000 [00:00<?, ? examples/s]

In [40]:
result

array([[0., 1., 0., 0.],
       [0., 1., 0., 0.],
       [0., 0., 0., 1.],
       ...,
       [0., 1., 1., 0.],
       [0., 0., 0., 1.],
       [0., 0., 0., 1.]], dtype=float32)

### ハイパラチューニング

In [9]:
# データの読み込み
data, class_name = load_dataset_4class_Multi_classification(f"{DATASET_PATH}/lifestory_GPT+human_annotation.xlsx")

In [10]:
# testデータと訓練に使用するデータに分割
dataset, eval_data = split_multilabel_data(data=data, test_size=0.2, SEED=SEED)

In [11]:
print(np.array(dataset['labels']).sum(axis=0))
print(np.array(eval_data['labels']).sum(axis=0))

[ 46 122 272 361]
[11 31 68 90]


In [13]:
# 最大トークン数
MAX_LEN = 128
# バッチサイズ
# BATCH_SIZE = 16
# エポック数
NUM_EPOCHS = 100
# 学習率
# LEARNING_RATE = 2e-5
# Cross Validation時のFold数
NUM_FOLDS = 5
# 早期停止のための忍耐値
PATIENCE = 3
# 乱数シード
SEED = 2024
# クラス数
NUM_LABELS = 4
# 閾値
THRESH = 0.5

In [14]:
# 東北大BERT-v3
MODEL_NAME = 'cl-tohoku/bert-base-japanese-v3'

In [12]:
import optuna

In [17]:
def objective(trial):
    # チューニングするハイパーパラメータの設定
    learning_rate = trial.suggest_loguniform('learning_rate', 1e-5, 1e-3)
    batch_size = trial.suggest_categorical('batch_size', [8, 16, 32])
    Classifier_model = MultiClassClassifier(model_name=MODEL_NAME, num_labels=NUM_LABELS, seed=SEED, thresh=THRESH)
    trainer = Classifier_model.train_model(dataset, eval_data, MAX_LEN, NUM_EPOCHS, learning_rate, batch_size, PATIENCE, output_dir)
    eval_result = trainer.evaluate()
    return eval_result["eval_macro_f1"]

In [18]:
# Optunaのスタディを作成して最適化を実行
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=10)

[I 2024-07-24 19:30:40,223] A new study created in memory with name: no-name-4f97d62b-7fb4-47a4-929f-b676c6ffd0cd
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at cl-tohoku/bert-base-japanese-v3 and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Map:   0%|          | 0/776 [00:00<?, ? examples/s]

Map:   0%|          | 0/193 [00:00<?, ? examples/s]

wandb: WARNING Source type is set to 'repo' but some required information is missing from the environment. A job will not be created from this run. See https://docs.wandb.ai/guides/launch/create-job


[I 2024-07-24 19:32:20,817] Trial 0 finished with value: 0.5713600617723925 and parameters: {'learning_rate': 9.316263656504444e-05, 'batch_size': 8}. Best is trial 0 with value: 0.5713600617723925.
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at cl-tohoku/bert-base-japanese-v3 and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


...

[I 2024-07-24 19:43:51,110] Trial 8 finished with value: 0.4163772352725842 and parameters: {'learning_rate': 2.5222916929152804e-05, 'batch_size': 32}. Best is trial 0 with value: 0.5713600617723925.
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at cl-tohoku/bert-base-japanese-v3 and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Map:   0%|          | 0/776 [00:00<?, ? examples/s]

Map:   0%|          | 0/193 [00:00<?, ? examples/s]

wandb: WARNING Source type is set to 'repo' but some required information is missing from the environment. A job will not be created from this run. See https://docs.wandb.ai/guides/launch/create-job


[I 2024-07-24 19:44:56,134] Trial 9 finished with value: 0.2795929941057059 and parameters: {'learning_rate': 0.0006251283298503759, 'batch_size': 16}. Best is trial 0 with value: 0.5713600617723925.


In [19]:
print("Best trial:")
trial = study.best_trial
print(f"  Value: {trial.value}")
print("  Params: ")
for key, value in trial.params.items():
    print(f"    {key}: {value}")

Best trial:
  Value: 0.5713600617723925
  Params: 
    learning_rate: 9.316263656504444e-05
    batch_size: 8


### majority classの精度

In [8]:
print(np.array(dataset['labels']).sum(axis=0))

[ 49 125 279 374]


In [10]:
# テストサイズ×マルチラベル数の二次元リスト
majority_pred = [[0 for i in range(4)] for j in range(len(test_data['labels']))]
for i in range(len(test_data['labels'])):
    majority_pred[i][-1] = 1

In [11]:
# accuracyを計算
accuracy = round(accuracy_score(y_true=test_data['labels'], y_pred=majority_pred), 3)
# macro f1を計算
macro_f1 = round(f1_score(y_true=test_data['labels'], y_pred=majority_pred, average='macro', zero_division=0), 3)
# クラス毎のF1値を計算
class_f1 = [round(score, 3) for score in f1_score(y_true=test_data['labels'], y_pred=majority_pred, average=None, zero_division=0)]
# クラス毎のrecallを計算
class_recall = [round(score, 3) for score in recall_score(y_true=test_data['labels'], y_pred=majority_pred, average=None, zero_division=0)]
# クラス毎のprecisionを計算
class_precision = [round(score, 3) for score in precision_score(y_true=test_data['labels'], y_pred=majority_pred, average=None, zero_division=0)]
print("Average accuracy:", accuracy)
print("Average Macro f1:", macro_f1)
print("Average Class f1:", class_f1)
print("Average Class recall:", class_recall)
print("Average Class precision:", class_precision)

Average accuracy: 0.463
Average Macro f1: 0.158
Average Class f1: [0.0, 0.0, 0.0, 0.633]
Average Class recall: [0.0, 0.0, 0.0, 1.0]
Average Class precision: [0.0, 0.0, 0.0, 0.463]


### 21クラスマルチクラス分類

In [6]:
# データの読み込み
data, class_name = load_multiclass_dataset(f"{DATASET_PATH}/act_classification_final.xlsx")

In [7]:
data_labels_np = np.array(data['labels'])
data_labels_np.sum(axis=0)

array([ 21,  12,  18,  46,   3,  56,  22,   1,  12,   4, 138,  28,  18,
        81,  11,  54,   5,   1,   6, 600])

In [8]:
# testデータと訓練に使用するデータに分割
dataset, test_data = split_multilabel_data(data=data, test_size=0.1, SEED=SEED)

In [9]:
print(np.array(dataset['labels']).sum(axis=0))
print(np.array(test_data['labels']).sum(axis=0))

[ 19  11  16  41   3  50  20   1  11   4 124  25  16  73  10  49   5   1
   5 540]
[ 2  1  2  5  0  6  2  0  1  0 14  3  2  8  1  5  0  0  1 60]


In [12]:
# 東北大BERT-v3
MODEL_NAME = 'cl-tohoku/bert-base-japanese-v3'
Classifier_model = MultiClassClassifier(model_name=MODEL_NAME, num_labels=20, seed=SEED, thresh=THRESH)

In [14]:
PATIENCE=10
result = Classifier_model.cross_validation(dataset, test_data, MAX_LEN, NUM_EPOCHS, LEARNING_RATE, BATCH_SIZE, PATIENCE, NUM_FOLDS, output_dir, project_name='ChatGPT_data_4class_weight')

-----------------Fold: 1-----------------


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at cl-tohoku/bert-base-japanese-v3 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Map:   0%|          | 0/655 [00:00<?, ? examples/s]

Map:   0%|          | 0/332 [00:00<?, ? examples/s]

wandb: WARNING Source type is set to 'repo' but some required information is missing from the environment. A job will not be created from this run. See https://docs.wandb.ai/guides/launch/create-job


...

Map:   0%|          | 0/658 [00:00<?, ? examples/s]

Map:   0%|          | 0/329 [00:00<?, ? examples/s]

wandb: WARNING Source type is set to 'repo' but some required information is missing from the environment. A job will not be created from this run. See https://docs.wandb.ai/guides/launch/create-job


Map:   0%|          | 0/113 [00:00<?, ? examples/s]

{'accuracy': 0.782608695652174, 'macro_f1': 0.20681159420289857, 'class_f1': [0.0, 0.0, 0.0, 0.8, 0.0, 0.8, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.667, 0.0, 0.0, 0.0, 0.87], 'class_recall': [0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.833], 'class_precision': [0.0, 0.0, 0.0, 0.667, 0.0, 0.667, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.5, 0.0, 0.0, 0.0, 0.909]}


In [15]:
# 重みありの場合の結果（cv=5）解答
average_accuracy = round(sum(d['accuracy'] for d in result)/len(result), 3)
average_macro_f1 = round(sum(d['macro_f1'] for d in result)/len(result), 3)
# クラスごとの平均値を計算
average_class_f1 = [round(sum(d['class_f1'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_f1']))]
average_class_recall = [round(sum(d['class_recall'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_recall']))]
average_class_precision = [round(sum(d['class_precision'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_precision']))]
print("Average accuracy:", average_accuracy)
print("Average Macro f1:", average_macro_f1)
print("Average Class f1:", average_class_f1)
print("Average Class recall:", average_class_recall)
print("Average Class precision:", average_class_precision)

Average accuracy: 0.739
Average Macro f1: 0.195
Average Class f1: [0.0, 0.0, 0.0, 0.83, 0.0, 0.489, 0.0, 0.0, 0.0, 0.0, 0.333, 0.0, 0.0, 0.79, 0.0, 0.622, 0.0, 0.0, 0.0, 0.828]
Average Class recall: [0.0, 0.0, 0.0, 1.0, 0.0, 0.5, 0.0, 0.0, 0.0, 0.0, 0.289, 0.0, 0.0, 0.778, 0.0, 0.833, 0.0, 0.0, 0.0, 0.844]
Average Class precision: [0.0, 0.0, 0.0, 0.711, 0.0, 0.556, 0.0, 0.0, 0.0, 0.0, 0.556, 0.0, 0.0, 0.833, 0.0, 0.5, 0.0, 0.0, 0.0, 0.816]


In [12]:
# 重みありの場合の結果（cv=5）
average_accuracy = round(sum(d['accuracy'] for d in result)/len(result), 3)
average_macro_f1 = round(sum(d['macro_f1'] for d in result)/len(result), 3)
# クラスごとの平均値を計算
average_class_f1 = [round(sum(d['class_f1'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_f1']))]
average_class_recall = [round(sum(d['class_recall'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_recall']))]
average_class_precision = [round(sum(d['class_precision'][i] for d in result) / len(result), 3) for i in range(len(result[0]['class_precision']))]
print("Average accuracy:", average_accuracy)
print("Average Macro f1:", average_macro_f1)
print("Average Class f1:", average_class_f1)
print("Average Class recall:", average_class_recall)
print("Average Class precision:", average_class_precision)

Average accuracy: 0.675
Average Macro f1: 0.212
Average Class f1: [0.0, 0.0, 0.0, 0.867, 0.0, 0.644, 0.222, 0.0, 0.0, 0.0, 0.301, 0.0, 0.333, 0.656, 0.0, 0.413, 0.0, 0.0, 0.0, 0.798]
Average Class recall: [0.0, 0.0, 0.0, 1.0, 0.0, 0.667, 0.167, 0.0, 0.0, 0.0, 0.389, 0.0, 0.333, 0.611, 0.0, 0.333, 0.0, 0.0, 0.0, 0.838]
Average Class precision: [0.0, 0.0, 0.0, 0.778, 0.0, 0.667, 0.333, 0.0, 0.0, 0.0, 0.25, 0.0, 0.333, 0.889, 0.0, 0.556, 0.0, 0.0, 0.0, 0.777]


In [46]:
# # 重みなしの場合の結果（cv=5）
# average_accuracy = round(sum(d['eval_accuracy'] for d in result)/len(result), 3)
# average_macro_f1 = round(sum(d['eval_macro_f1'] for d in result)/len(result), 3)
# # クラスごとの平均値を計算
# average_class_f1 = [round(sum(d['eval_class_f1'][i] for d in result) / len(result), 3) for i in range(len(result[0]['eval_class_f1']))]
# average_class_recall = [round(sum(d['eval_class_recall'][i] for d in result) / len(result), 3) for i in range(len(result[0]['eval_class_recall']))]
# average_class_precision = [round(sum(d['eval_class_precision'][i] for d in result) / len(result), 3) for i in range(len(result[0]['eval_class_precision']))]
# print("Average accuracy:", average_accuracy)
# print("Average Macro f1:", average_macro_f1)
# print("Average Class f1:", average_class_f1)
# print("Average Class recall:", average_class_recall)
# print("Average Class precision:", average_class_precision)

Average accuracy: 0.724
Average Macro f1: 0.15
Average Class f1: [0.0, 0.0, 0.0, 0.333, 0.0, 0.489, 0.0, 0.0, 0.0, 0.0, 0.424, 0.0, 0.0, 0.624, 0.0, 0.3, 0.0, 0.0, 0.0, 0.831]
Average Class recall: [0.0, 0.0, 0.0, 0.333, 0.0, 0.389, 0.0, 0.0, 0.0, 0.0, 0.39, 0.0, 0.0, 0.556, 0.0, 0.278, 0.0, 0.0, 0.0, 0.916]
Average Class precision: [0.0, 0.0, 0.0, 0.333, 0.0, 0.667, 0.0, 0.0, 0.0, 0.0, 0.532, 0.0, 0.0, 0.833, 0.0, 0.333, 0.0, 0.0, 0.0, 0.767]


### majority classの精度

In [10]:
print(np.array(dataset['labels']).sum(axis=0))

[ 19  11  16  41   3  50  20   1  11   4 124  25  16  73  10  49   5   1
   5 540]


In [28]:
# テストサイズ×マルチラベル数の二次元リスト
majority_pred = [[0 for i in range(20)] for j in range(len(test_data['labels']))]
for i in range(len(test_data['labels'])):
    majority_pred[i][-1] = 1

In [30]:
# accuracyを計算
accuracy = round(accuracy_score(y_true=test_data['labels'], y_pred=majority_pred), 3)
# macro f1を計算
macro_f1 = round(f1_score(y_true=test_data['labels'], y_pred=majority_pred, average='macro', zero_division=0), 3)
# クラス毎のF1値を計算
class_f1 = [round(score, 3) for score in f1_score(y_true=test_data['labels'], y_pred=majority_pred, average=None, zero_division=0)]
# クラス毎のrecallを計算
class_recall = [round(score, 3) for score in recall_score(y_true=test_data['labels'], y_pred=majority_pred, average=None, zero_division=0)]
# クラス毎のprecisionを計算
class_precision = [round(score, 3) for score in precision_score(y_true=test_data['labels'], y_pred=majority_pred, average=None, zero_division=0)]
print("Average accuracy:", accuracy)
print("Average Macro f1:", macro_f1)
print("Average Class f1:", class_f1)
print("Average Class recall:", class_recall)
print("Average Class precision:", class_precision)

Average accuracy: 0.531
Average Macro f1: 0.035
Average Class f1: [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.694]
Average Class recall: [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0]
Average Class precision: [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.531]


In [15]:
import numpy as np

In [17]:
data_labels_np = np.array(data['labels'])
data_labels_np.sum(axis=0)

array([ 21,  12,  18,  46,   3,  56,  22,   1,  12,   4, 138,  28,  18,
        81,  11,  54,   5,   1,   6, 600])

In [18]:
class_name

array(['1 - A. 睡眠', '1 - B. 身の回りの用事', '1 - C - a. 食事-飲酒あり',
       '1 - C - b. 食事-飲酒なし・不明', '2 - A - a. 通勤・通学', '2 - A - b. その他の移動',
       '2 - B. 仕事', '2 - C. 学業', '2 - D. 家事', '2 - F. 育児',
       '3 - A. メディア（テレビ・ラジオ・新聞・雑誌・ネット）', '3 - B. 買い物',
       '3 - C - a. 趣味・娯楽-体動かす', '3 - C - b. 趣味・娯楽-体動かさない',
       '3 - D - a. 交際-物理的接触', '3 - D - b. 交際-オンライン的接触', '3 - E. 受診・療養',
       '3 - F - a. 喫煙', '3 - F - b. その他の活動(事故など)', '4. 活動なし'],
      dtype=object)